In [ ]:
import pypsa
import numpy as np
import pandas as pd
import os
from pathlib import Path
import matplotlib.pyplot as plt

plt.style.use("ggplot")
import pycountry
import json
import warnings

warnings.filterwarnings("ignore")

In [ ]:
available_models = {
    "model_1": "elec_s_37_ec_lv1.0_.nc",
    "model_2": "elec_s_37_ec_lv1.0_3H_withUC.nc",
    "model_3": "elec_s_37_ec_lv1.0_Co2L-noUC-noCo2price.nc",
    "model_4": "elec_s_37_ec_lv1.0_Ep.nc",
    "model_5": "elec_s_37_ec_lv1.0_Ep_new.nc",
}

data_path = Path.cwd() / ".." / ".."
model_path = data_path / available_models["model_5"]

with open(data_path / "generation_data" / "generation_mapper_pypsa.json", "r") as f:
    pypsa_generation_mapper = json.load(f)

In [ ]:
n = pypsa.Network(str(model_path))

In [ ]:
def intersection(alist, blist):
    for val in alist:
        if val not in blist:
            alist.remove(val)
    return alist

In [ ]:
pypsa_generation_mapper

In [ ]:
countries = set([col[:2] for col in n.generators_t.p.columns])
gen = set([col[6:] for col in n.generators_t.p.columns])

for i, country in enumerate(countries):
    df = pd.DataFrame(index=n.generators_t.p.index)
    # country_generation = [col for col in n.generators_t.p.columns if col.startswith(country)]
    country_generation = n.generators.loc[n.generators.bus.str.contains(country)]

    for key, gens in pypsa_generation_mapper.items():
        # curr_gen = country_generation.loc[
        #     (country_generation.carrier.str.contains(tech) for tech in gens).astype(bool)].index
        curr_gen = country_generation.loc[
            country_generation.carrier.apply(lambda carr: carr in gens)
        ].index

        if len(curr_gen):
            df[key] = n.generators_t.p[curr_gen].mean(axis=1)
        else:
            df[key] = np.zeros(len(df))

    df.to_csv(data_path / "pypsa_data" / (country + ".csv"))

In [ ]:
import seaborn as sns


for num, country in enumerate(os.listdir(data_path / "pypsa_data")):
    # country = "DE.csv"
    cc = country[:2]

    pypsa_df = pd.read_csv(
        data_path / "pypsa_data" / country, parse_dates=True, index_col=0
    )
    try:
        entsoe_df = pd.read_csv(
            data_path / "harmonised_generation_data" / ("prepared_" + country),
            parse_dates=True,
            index_col=0,
        )

        entsoe_df.columns = [col[:-6] for col in entsoe_df.columns]
    except FileNotFoundError:
        continue

    fig, axs = plt.subplots(3, 3, figsize=(20, 15))

    axs[0, 0].set_title(pycountry.countries.get(alpha_2=country[:2]).name)

    start = pd.Timestamp("2019-01-01")  # for small time frame
    end = pd.Timestamp("2019-01-14")
    coarse_freq = "d"

    num_techs_shown = 6

    links = n.links.loc[
        (n.links.bus0.str.contains(cc) + n.links.bus1.str.contains(cc)).astype(bool)
    ]
    links = links.loc[links.carrier == "DC"].sum(axis=1)

    from_here = n.links.loc[links.index].bus0.str.contains(cc)
    to_here = n.links.loc[links.index].bus1.str.contains(cc)

    pypsa_df["Import Export"] = pd.concat(
        (n.links_t.p0[from_here.index], n.links_t.p0[to_here.index]), axis=1
    ).sum(axis=1)

    # show_techs = pypsa_df.sum().sort_values(ascending=False).iloc[:num_techs_shown].index.tolist()
    show_techs = (
        entsoe_df.sum()
        .sort_values(ascending=False)
        .iloc[:num_techs_shown]
        .index.tolist()
    )

    entsoe_df[intersection(show_techs, entsoe_df.columns.tolist())].loc[start:end].plot(
        ax=axs[0, 0]
    )
    pypsa_df[show_techs].loc[start:end].plot(ax=axs[0, 1], legend=False)

    pypsa_load = n.loads_t.p_set
    pypsa_load = pypsa_load[
        [col for col in pypsa_load.columns if col.startswith(country[:2])]
    ].mean(axis=1)

    pypsa_load.loc[start:end].plot(ax=axs[0, 2])

    axs[0, 0].set_ylabel("ENTSOE Generation")
    axs[0, 1].set_ylabel("PyPSA Generation")
    axs[0, 2].set_ylabel("PyPSA Load")

    upper_lim = pd.concat((pypsa_df, entsoe_df), axis=0).max().max()
    for ax in axs[0, :2]:
        ax.set_ylim(0, upper_lim)

    for ax in axs[0, :2]:
        ax.legend()

    # entsoe_df[[col+" (MWh)" for col in pypsa_df.columns]].loc[start:end].plot(ax=axs[0])
    entsoe_df[intersection(show_techs, entsoe_df.columns.tolist())].resample(
        coarse_freq
    ).mean().plot(ax=axs[1, 0])
    pypsa_df[show_techs].resample(coarse_freq).mean().plot(ax=axs[1, 1], legend=False)

    pypsa_load = n.loads_t.p_set
    pypsa_load = pypsa_load[
        [col for col in pypsa_load.columns if col.startswith(country[:2])]
    ].mean(axis=1)
    pypsa_load.resample(coarse_freq).sum().plot(ax=axs[1, 2])

    # pypsa_df[show_techs].resample(coarse_freq).mean().sum(axis=1).plot(ax=axs[1,2], legend=False)

    axs[1, 0].set_ylabel("ENTSOE Generation")
    axs[1, 1].set_ylabel("PyPSA Generation")
    axs[1, 2].set_ylabel("PyPSA Load")

    upper_lim = (
        pd.concat(
            (
                pypsa_df.resample(coarse_freq).mean(),
                entsoe_df.resample(coarse_freq).mean(),
            ),
            axis=0,
        )
        .max()
        .max()
    )
    for ax in axs[1, :2]:
        ax.set_ylim(0, upper_lim)

    for ax in axs[1, :2]:
        ax.legend()

    try:
        entsoe_prices = pd.read_csv(
            data_path / "price_data" / country,
            index_col=0,
            parse_dates=True,
        )

        def make_tz_time(time):
            return pd.Timestamp(time).tz_convert("utc")

        entsoe_prices.index = pd.Series(entsoe_prices.index).apply(
            lambda time: make_tz_time(time)
        )
        entsoe_prices.resample("3d").mean().plot(ax=axs[2, 0])

    except FileNotFoundError:
        pass

    prices_col = [
        col for col in n.buses_t.marginal_price.columns if col.startswith(country[:2])
    ]
    pypsa_prices = n.buses_t.marginal_price[prices_col].mean(axis=1)
    pypsa_prices.resample("3d").mean().plot(ax=axs[2, 1])

    upper_lim = pd.concat((entsoe_prices, pypsa_prices), axis=0).max().max()
    for ax in axs[2, :2]:
        ax.set_ylim(0, upper_lim)

    axs[2, 0].set_ylabel("ENTSOE Day Ahead Prices")
    axs[2, 1].set_ylabel("PyPSA Shadow Prices")

    pypsa_totals = pypsa_df.sum()

    entsoe_totals = entsoe_df.sum()
    totals = pd.DataFrame(index=pypsa_totals.index)

    totals["pypsa"] = pypsa_totals
    totals["entsoe"] = entsoe_totals
    entsoe_totals.loc["Import Export"] = 0.0
    totals["tech"] = totals.index

    totals = pd.concat(
        [
            pd.DataFrame(
                {
                    "kind": ["pypsa" for _ in range(len(pypsa_totals))],
                    "tech": pypsa_totals.index,
                    "total generation": pypsa_totals.values,
                }
            ),
            pd.DataFrame(
                {
                    "kind": ["entsoe" for _ in range(len(entsoe_totals))],
                    "tech": entsoe_totals.index,
                    "total generation": entsoe_totals.values,
                }
            ),
        ],
        axis=0,
    )

    sns.barplot(
        data=totals,
        x="tech",
        y="total generation",
        hue="kind",
        ax=axs[2, 2],
        palette="dark",
        alpha=0.6,
        edgecolor="k",
    )
    axs[2, 2].set_ylabel("Total Generation")
    axs[2, 2].set_xticks(
        axs[2, 2].get_xticks(), axs[2, 2].get_xticklabels(), rotation=45, ha="right"
    )

    plt.tight_layout()
    plt.show()

    if num == 7:
        break


# df.to_csv(data_path / "pypsa_data" / (country+".csv"))

In [ ]:
links = n.links.loc[
    (n.links.bus0.str.contains("DE") + n.links.bus1.str.contains("DE")).astype(bool)
]
links = links.loc[links.carrier == "DC"].sum(axis=1)
n.links_t.p0[links.index.tolist()].resample("w").sum().plot()

In [ ]:
german_origin = n.links.loc[links.index].bus0.str.contains("DE")
german_destin = n.links.loc[links.index].bus1.str.contains("DE")

net_impexp = pd.concat(
    (n.links_t.p0[german_origin.index], n.links_t.p0[german_destin.index]), axis=1
).sum(axis=1)

net_impexp.iloc[:200].plot()